In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
os.environ['EMAIL']='pjh8723@gmail.com'

In [3]:
import sys
sys.path.append('/home/jovyan/chemix/src/')

In [4]:
os.environ

environ{'SHELL': '/bin/bash',
        'HOSTNAME': '0f4a3ec8c60f',
        'LANGUAGE': 'en_US.UTF-8',
        'NB_UID': '1000',
        'JULIA_PKGDIR': '/opt/julia',
        'PWD': '/home/jovyan',
        'HOME': '/home/jovyan',
        'LANG': 'en_US.UTF-8',
        'NB_GID': '100',
        'JULIA_VERSION': '1.5.2',
        'XDG_CACHE_HOME': '/home/jovyan/.cache/',
        'JUPYTER_ENABLE_LAB': 'yes',
        'SHLVL': '0',
        'CONDA_DIR': '/opt/conda',
        'MINICONDA_VERSION': '4.8.3',
        'JULIA_DEPOT_PATH': '/opt/julia',
        'CONDA_VERSION': '4.9.0',
        'NB_USER': 'jovyan',
        'LC_ALL': 'en_US.UTF-8',
        'PATH': '/opt/conda/bin:/usr/local/sbin:/usr/local/bin:/usr/sbin:/usr/bin:/sbin:/bin',
        'DEBIAN_FRONTEND': 'noninteractive',
        'JPY_PARENT_PID': '6',
        'TERM': 'xterm-color',
        'CLICOLOR': '1',
        'PAGER': 'cat',
        'GIT_PAGER': 'cat',
        'MPLBACKEND': 'module://ipykernel.pylab.backend_inline',
        'EMAIL': '

In [5]:
import logging
logging.basicConfig(format='[%(process)d] %(levelname)s: %(message)s', level=logging.INFO)

In [6]:
import chexmix.datasources.base as ds
import chexmix.datasources.entrez as ez
import chexmix.datasources.pubtator as pt
import chexmix.datasources.taxonomy as tax
import chexmix.datasources.mesh as mesh

import chexmix.visualization.circle_packing as cp

from IPython.display import JSON

In [7]:
%%time
tt = tax.load_taxonomy()

[604] INFO: load /home/jovyan/chemix/data/taxonomy_pbj.pkl


CPU times: user 4.86 s, sys: 502 ms, total: 5.36 s
Wall time: 6.14 s


# kpeb data load

In [8]:
with open('./KPEB_name_taxoID.txt','r',encoding='utf8') as f:
    data = f.read().splitlines()
data = list(map(lambda x: x.split('\t'), data))
data = list(filter(lambda x: x[1]!='', data))
data = {v: k for k, v in dict(data).items()}

# 같은 family, genus에 속하는 정보 가져오는 함수
## return (taxoID, Name, dept)

In [9]:
def children(nodes,depth=0):
    depth += 1
    l = []
    for node in nodes:
        tmp = children(node['children'], depth)
        l = l + (tmp)
        l.append((node['id'], (node['name'], depth)))
    return l
    


In [202]:
def children_hier(nodes, data, input_name):
    l = {}
    for node in nodes:
        if node['name'] == input_name:
            continue
        tmp = children_hier(node['children'],data, input_name)
        if str(node['id']) not in data:
            l[f"{node['id']}: {node['name']}"] = tmp
        else:
            l[f"========KPEB : {node['id']}: {node['name']}========"] = tmp
       # l[f"{node['id']}: {node['name']}"] = tmp
    return l
    


In [203]:
genus_list = children_hier(tt[genus_id]['children'], data, input_name)

In [204]:
family_list = children_hier(tt[family_id]['children'], data, input_name)

In [206]:
JSON(genus_list)

<IPython.core.display.JSON object>

In [133]:
genus_list

[(59501, ('Rubus idaeus subsp. idaeus', 2)),
 (59503, ('Rubus idaeus subsp. strigosus', 2)),
 (2697234, ('Rubus idaeus var. aculeatissimus', 2)),
 (32247, ('Rubus idaeus', 1)),
 (43104, ('Rubus hispidus', 1)),
 (57936, ('Rubus chamaemorus', 1)),
 (59490, ('Rubus argutus', 1)),
 (59491, ('Rubus cuneifolius', 1)),
 (616956, ('Rubus ellipticus var. obcordatus', 2)),
 (59492, ('Rubus ellipticus', 1)),
 (59493, ('Rubus hawaiensis', 1)),
 (59494, ('Rubus macraei', 1)),
 (59495, ('Rubus niveus', 1)),
 (59496, ('Rubus parviflorus', 1)),
 (59497, ('Rubus rigidus', 1)),
 (59498, ('Rubus rosifolius', 1)),
 (59499, ('Rubus spectabilis', 1)),
 (59502, ('Rubus sachalinensis', 1)),
 (190231, ('Rubus arcticus subsp. stellatus', 2)),
 (669800, ('Rubus arcticus subsp. acaulis', 2)),
 (70741, ('Rubus arcticus', 1)),
 (75061, ('Rubus repens', 1)),
 (75062, ('Rubus allegheniensis', 1)),
 (75063, ('Rubus alpinus', 1)),
 (75064, ('Rubus bifrons', 1)),
 (75065, ('Rubus caesius', 1)),
 (75066, ('Rubus canadens

# KPEB 필터링 함수

In [10]:
def filter_KPEB(dic, kpeb):
    ret = {}
    for d in dic:
        if str(d) in kpeb:
            ret[d]=dic[d][0]
    
    return ret

# genus, family명 가져오기

In [122]:
input_name = 'Rubus coreanus'

In [123]:
for tmp in tt:
    if tt[tmp]['name'] == input_name:
        family = tt[tmp]['family']
        genus = tt[tmp]['genus']
        break;

In [124]:
family

'Rosaceae'

# genus, family taxoID가져오기

In [126]:
count = 0
for tmp in tt:
    if tt[tmp]['name'] == genus:
        genus_id = tmp
        count += 1
    if tt[tmp]['name'] == family:
        family_id = tmp
        count += 1
    if count == 2:
        break

In [132]:
family_list = children(tt[family_id]['children'])
genus_list = children(tt[genus_id]['children'])

In [20]:
#family 내 genus리스트 삭제
family_list = list(filter(lambda x: x not in genus_list, family_list))

In [16]:
for g in genus_list:
    if g[1][0] == input_name:
        d = g[1][1]
        break

In [22]:
genus_dict = dict(genus_list)
family_dict = dict(family_list)

1

In [23]:
JSON(filter_KPEB(genus_dict, data))

<IPython.core.display.JSON object>

In [24]:
JSON(filter_KPEB(family_dict, data))

<IPython.core.display.JSON object>

In [31]:
%%time
tt = tax.load_taxonomy()
tt = ds.add_pmids(tt, at, 'TAXO:', 1)
ds.trim_tree(tt[1])
None


[941] INFO: save /home/jovyan/chemix/data/taxonomy.pkl
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 39059 does not exist
[941] WARNING: 74724 does not exist
[941] WARNING: 74724 does not exist
[941] WARNING: 74724 does not exist
[941] WARNING: 39059 does not exist


CPU times: user 3min 9s, sys: 6.46 s, total: 3min 16s
Wall time: 3min 30s


In [32]:
%%time
mt = mesh.load_mesh()
mt = ds.add_pmids(mt, at, 'MESH:', 'root')
ds.trim_tree(mt['root'])
None

[941] INFO: load /home/jovyan/chemix/data/mesh/MESH_FILES/xmlmesh/desc2020.xml
[941] INFO: load /home/jovyan/chemix/data/mesh/MESH_FILES/xmlmesh/qual2020.xml
[941] INFO: load /home/jovyan/chemix/data/mesh/MESH_FILES/xmlmesh/supp2020.xml
[941] INFO: save /home/jovyan/chemix/data/mesh.pkl


CPU times: user 1min 2s, sys: 3.09 s, total: 1min 5s
Wall time: 1min 22s


In [154]:
JSON(ds.to_json(tt[1], 
                name_func=lambda n: f"{len(n['total_pmids'])}:{n['id']}:{n['name']}", 
                sort_key=lambda n: -len(n['total_pmids'])))

KeyError: 'total_pmids'

In [34]:
JSON(ds.to_json(mt['root'], 
                name_func=lambda n: f"{len(n['total_pmids'])}:{n['id']}:{n['name']}", 
                sort_key=lambda n: -len(n['total_pmids'])))

<IPython.core.display.JSON object>

In [35]:
cp.init()

<IPython.core.display.Javascript object>

In [36]:
cp.draw(tt[1], normalize_func=lambda n: {'name': n['name'], 
                                         'value': 1 + len(n['total_pmids']), 
                                         'children': n['children']})

<IPython.core.display.Javascript object>

In [18]:
cp.draw(mt['root'], normalize_func=lambda n: {'name': n['name'], 
                                              'value': 1 + len(n['total_pmids']), 
                                              'children': n['children']})

<IPython.core.display.Javascript object>